# **Boosting Wav2Vec2 with n-grams in 🤗 Transformers**

**Wav2Vec2** is a popular pre-trained model for speech recognition. Released in [September 2020](https://ai.facebook.com/blog/wav2vec-20-learning-the-structure-of-speech-from-raw-audio/) by Meta AI Research, the novel architecture catalyzed progress in self-supervised pretraining for speech recognition, *e.g.* [*G. Ng et al.*, 2021](https://arxiv.org/pdf/2104.03416.pdf), [*Chen et al*, 2021](https://arxiv.org/abs/2110.13900), [*Hsu et al.*, 2021](https://arxiv.org/abs/2106.07447) and [*Babu et al.*, 2021](https://arxiv.org/abs/2111.09296). On the Hugging Face Hub, Wav2Vec2's most popular pre-trained checkpoint currently amounts to over [**250,000** monthly downloads](https://huggingface.co/facebook/wav2vec2-base-960h).

Using Connectionist Temporal Classification (CTC), pre-trained Wav2Vec2-like checkpoints are extremely easy to fine-tune on downstream speech recognition tasks.
In a nutshell, fine-tuning pre-trained Wav2Vec2 checkpoints works as follows: 

A single randomly initialized linear layer is stacked on top of the pre-trained checkpoint and trained to classify raw audio input to a sequence of letters. It does so by:

1.  extracting audio representations from the raw audio (using CNN layers),
2. processing the sequence of audio representations with a stack of transformer layers, and,
3. classifying the processed audio representations into a sequence of output letters.

Previously audio classification models required an additional language model (LM) and a dictionary to transform the sequence of classified audio frames to a coherent transcription.
Wav2Vec2's architecture is based on transformer layers, thus giving each processed audio representation context 
from all other audio representations. In addition, 
Wav2Vec2 leverages the [CTC algorithm](https://distill.pub/2017/ctc/) for fine-tuning, which solves the problem of alignment between a varying "input audio length"-to-"output text length" ratio.

Having contextualized audio classifications and no alignment problems, Wav2Vec2 does not require 
an external language model or dictionary to yield acceptable audio transcriptions.

As can be seen in Appendix C of the [official paper](https://arxiv.org/abs/2006.11477), Wav2Vec2 gives impressive downstream performances on [LibriSpeech]((https://huggingface.co/datasets/librispeech_asr)) without using a language model at all. However, from the appendix, it also becomes clear that using Wav2Vec2 in combination with a language model can yield a significant improvement, especially when the model was trained on only 10 minutes of transcribed audio.

Until recently, the 🤗 Transformers library did not offer a simple user interface to decode audio files with a fine-tuned Wav2Vec2 **and** a language model. This has thankfully changed. 🤗 Transformers now offers an easy-to-use integration with *Kensho Technologies'* [pyctcdecode library](https://github.com/kensho-technologies/pyctcdecode). This blog post is a step-by-step **technical** guide to explain how one can create an **n-gram** language model and combine it with an existing fine-tuned Wav2Vec2 checkpoint using 🤗 Datasets and 🤗 Transformers.

We start by:

1. How does decoding audio with an LM differ from decoding audio without an LM?
2. How to get suitable data for a language model?
3. How to build an *n-gram* with KenLM?
4. How to combine the *n-gram* with a fine-tuned Wav2Vec2 checkpoint?

For a deep dive into how Wav2Vec2 functions - which is not necessary for this blog post - the reader is advised to consult the following material:

- [wav2vec 2.0: A Framework for Self-Supervised Learning of Speech Representations](https://arxiv.org/abs/2006.11477)
- [Fine-Tune Wav2Vec2 for English ASR with 🤗 Transformers](https://huggingface.co/blog/fine-tune-wav2vec2-english)
- [An Illustrated Tour of Wav2vec 2.0](https://jonathanbgn.com/2021/09/30/illustrated-wav2vec-2.html)

## **1. Decoding audio data with Wav2Vec2 and a language model**

As shown in 🤗 Transformers [exemple docs of Wav2Vec2](https://huggingface.co/docs/transformers/master/en/model_doc/wav2vec2#transformers.Wav2Vec2ForCTC), audio can be transcribed as follows.

First, we install `datasets` and `transformers`.



In [1]:
!pip install -U datasets transformers

     |████████████████████████████████| 311 kB 24.2 MB/s            
  Attempting uninstall: datasets
    Found existing installation: datasets 1.18.2.dev0
    Uninstalling datasets-1.18.2.dev0:
ERROR: Could not install packages due to an OSError: [Errno 13] Permission denied: 'WHEEL'
Consider using the `--user` option or check the permissions.

You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.


Let's load a small excerpt of the [Librispeech dataset](https://huggingface.co/datasets/librispeech_asr) to demonstrate Wav2Vec2's speech transcription capabilities.

In [ ]:
from datasets import load_dataset

dataset = load_dataset("hf-internal-testing/librispeech_asr_demo", "clean", split="validation")
dataset

Reusing dataset librispeech_asr (/root/.cache/huggingface/datasets/hf-internal-testing___librispeech_asr/clean/2.1.0/f2c70a4d03ab4410954901bde48c54b85ca1b7f9bf7d616e7e2a72b5ee6ddbfc)


Dataset({
    features: ['file', 'audio', 'text', 'speaker_id', 'chapter_id', 'id'],
    num_rows: 73
})

We can pick one of the 73 audio samples and listen to it.

In [ ]:
import IPython.display as ipd

audio_sample = dataset[2]
print(audio_sample["text"].lower())
ipd.Audio(data=audio_sample["audio"]["array"], autoplay=True, rate=audio_sample["audio"]["sampling_rate"])

he tells us that at this festive season of the year with christmas and roast beef looming before us similes drawn from eating and its results occur most readily to the mind


Having chosen a data sample, we now load the fine-tuned model and processor.

In [ ]:
from transformers import Wav2Vec2Processor, Wav2Vec2ForCTC

processor = Wav2Vec2Processor.from_pretrained("facebook/wav2vec2-base-100h")
model = Wav2Vec2ForCTC.from_pretrained("facebook/wav2vec2-base-100h")

Next, we process the data

In [ ]:
inputs = processor(audio_sample["audio"]["array"], sampling_rate=16_000, return_tensors="pt")

forward it to the model

In [ ]:
import torch

with torch.no_grad():
  logits = model(**inputs).logits

and decode it

In [ ]:
predicted_ids = torch.argmax(logits, dim=-1)
transcription = processor.batch_decode(predicted_ids)

transcription[0].lower()

'he tells us that at this festive season of the year with christmaus and rose beef looming before us simalyis drawn from eating and its results occur most readily to the mind'

Comparing the transcription to the target transcription above, we can see that some words *sound* correct, but are not *spelled* correctly, *e.g.*:

- *christmaus* vs. *christmas*
- *rose* vs. *roast*
- *simalyis* vs. *similes*

Let's see whether combining Wav2Vec2 with an ***n-gram*** lnguage model can help here.

First, we need to install `pyctcdecode` and `kenlm`.

In [2]:
!pip install https://github.com/kpu/kenlm/archive/master.zip pyctcdecode

     \ 541 kB 1.8 MB/s
  Preparing metadata (setup.py) ... done
     |████████████████████████████████| 43 kB 7.0 MB/s             
     |████████████████████████████████| 376 kB 55.0 MB/s            
  Preparing metadata (setup.py) ... done
  Created wheel for kenlm: filename=kenlm-0.0.0-cp38-cp38-linux_x86_64.whl size=2345337 sha256=dc0d81c6f059a5f0841cf0f6a4ca235cae715d4f9f52a9311e67989f64782ae3
  Stored in directory: /tmp/pip-ephem-wheel-cache-7xk1d9qa/wheels/ff/08/4e/a3ddc0e786e0f3c1fcd2e7a82c4324c02fc3ae2638471406d2
  Created wheel for pygtrie: filename=pygtrie-2.4.2-py3-none-any.whl size=19063 sha256=ea48bfe279335b62a3582df18a9f3b64abb89e71bb06753eea974f57f03f97e7
  Stored in directory: /workspace/.cache/pip/wheels/31/03/7b/f685b394a937bc97d2d40908d45aa31f3d9473bca6e9019153
Successfully built kenlm pygtrie
You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.


For demonstration purposes, we have prepared a new model repository [patrickvonplaten/wav2vec2-base-100h-with-lm](https://huggingface.co/patrickvonplaten/wav2vec2-base-100h-with-lm) which contains the same Wav2Vec2 checkpoint but has an additional **4-gram** language model for English.

Instead of using `Wav2Vec2Processor`, this time we use `Wav2Vec2ProcessorWithLM` to load the **4-gram** model in addition to the feature extractor and tokenizer.

In [ ]:
from transformers import Wav2Vec2ProcessorWithLM

processor = Wav2Vec2ProcessorWithLM.from_pretrained("patrickvonplaten/wav2vec2-base-100h-with-lm")

In constrast to decoding the audio without language model, the processor now directly receives the model's output `logits` instead of the `argmax(logits)` (called `predicted_ids`) above. The reason is that when decoding with a language model, at each time step, the processor takes the probabilities of all possible output characters into account. Let's take a look at the dimension of the `logits` output.

In [ ]:
logits.shape

torch.Size([1, 624, 32])

We can see that the `logits` correspond to a sequence of 624 vectors each having 32 entries. Each of the 32 entries thereby stands for the logit probability of one of the 32 possible output characters of the model:

In [ ]:
" ".join(sorted(processor.tokenizer.get_vocab()))

"' </s> <pad> <s> <unk> A B C D E F G H I J K L M N O P Q R S T U V W X Y Z |"

Intuitively, one can understand the decoding process of `Wav2Vec2ProcessorWithLM` as applying beam search through a matrix of size 624 $\times$ 32 probabilities while leveraging the probabilities of the next letters as given by the *n-gram* language model.

OK, let's run the decoding step again. `pyctcdecode` language model decoder does not automatically convert `torch` tensors to `numpy` so we'll have to convert them ourselves before.

In [ ]:
transcription = processor.batch_decode(logits.numpy()).text
transcription[0].lower()

'he tells us that at this festive season of the year with christmas and rose beef looming before us similes drawn from eating and its results occur most readily to the mind'

Cool! Recalling the words `facebook/wav2vec2-base-100h` without a language model transcribed incorrectly previously, *e.g.*,

> - *christmaus* vs. *christmas*
- *rose* vs. *roast*
- *simalyis* vs. *similes*

we can take another look at the transcription of `facebook/wav2vec2-base-100h` **with** a 4-gram language model. 2 out of 3 errors are corrected; *christmas* and *similes* have been correctly transcribed.

Interestingly, the incorrect transcription of *rose* persists. However, this should not surprise us very much. Decoding audio without a language model is much more prone to yield spelling mistakes, such as *christmaus* or *similes* (those words don't exist in the English language as far as I know). This is because the speech recognition system almost solely bases its prediction on the acoustic input it was given and not really on the language modeling context of previous and successive predicted letters ${}^1$. 
If on the other hand, we add a language model, we can be fairly sure that the speech recognition system will heavily reduce spelling errors since a well-trained *n-gram* model will surely not predict a word that has spelling errors. But the word *rose* is a valid English word and therefore the 4-gram will predict this word with a probability that is not insignificant. 

The language model on its own most likely does favor the correct word *roast* since the word sequence *roast beef* is much more common in English than *rose beef*. Because the final transcription is derived from a weighted combination of `facebook/wav2vec2-base-100h` output probabilities and those of the *n-gram* language model, it is quite common to see incorrectly transcribed words such as *rose*.

For more information on how you can tweak different parameters when decoding with `Wav2Vec2ProcessorWithLM`, please take a look at the official documentation [here](https://huggingface.co/docs/transformers/master/en/model_doc/wav2vec2#transformers.Wav2Vec2ProcessorWithLM.batch_decode).

---
${}^1$ Some research shows that a model such as `facebook/wav2vec2-base-100h` - when sufficiently large and trained on enough data - can learn language modeling dependencies between intermediate audio representations similar to a language model.


Great, now that you have seen the advantages adding an *n-gram* language model can bring, let's dive into how to create an *n-gram* and `Wav2Vec2ProcessorWithLM` from scratch.

## **2. Getting data for your language model**

A language model that is useful for a speech recognition system should support the acoustic model, *e.g.* Wav2Vec2, in predicting the next word (or token, letter) and therefore model the following distribution:

$\mathbf{P}(w_n | \mathbf{w}_0^{t-1})$ with $w_n$ being the next word and $\mathbf{w}_0^{t-1}$ being the sequence of all previous words since the beginning of the utterance. Simply said, the language model should be good at predicting the next word given all previously transcribed words regardless of the audio input given to the speech recognition system.

As always a language model is only as good as the data it is trained on. In the case of speech recognition, we should therefore ask ourselves for what kind of data, the speech recognition will be used for: *conversations*, *audiobooks*, *movies*, *speeches*, *, etc*, ...?

The language model should be good at modeling language that corresponds to the 
target transcriptions of the speech recognition system. 
For demonstration purposes, we assume here that we have fine-tuned a pre-trained [`facebook/wav2vec2-xls-r-300m`](https://huggingface.co/facebook/wav2vec2-xls-r-300m) on [Common Voice 7](https://huggingface.co/datasets/mozilla-foundation/common_voice_7_0) in Swedish. The fine-tuned checkpoint can 
be found [here](https://huggingface.co/hf-test/xls-r-300m-sv).
Common Voice 7 is a relatively crowd-sourced read-out audio dataset and we will evaluate the model on its test data.

Let's now look for suitable text data on the Hugging Face Hub. We search all datasets for those [that contain Swedish data](https://huggingface.co/datasets?languages=languages:sv&sort=downloads). 
Browsing a bit through the datasets, we are looking for a dataset that is similar to Common Voice's read-out audio data. The obvious choices of [oscar](https://huggingface.co/datasets/oscar) and [mc4](https://huggingface.co/datasets/mc4) might not be the most suitable here because they:

- are generated from crawling the web, which might not be very clean and correspond well to spoken language
- require a lot of pre-processing
- are very large which is not ideal for demonstration purposes here 😉

A dataset that seems sensible here and which is relatively clean and easy to pre-process is [europarl_bilingual](https://huggingface.co/datasets/europarl_bilingual) as it's a dataset that is based on discussions and talks of the European parliament. It should therefore be relatively clean and correspond well to read-out audio data. The dataset is originally designed for machine translation and can therefore only be accessed in translation pairs. We will only extract the text of the target language, Swedish (`sv`), from the *English-to-Swedish* translations.

In [3]:
target_lang="en"  # change to your target lang

Let's download the data.

In [4]:
from datasets import load_dataset

dataset = load_dataset("news_commentary", lang1="ar", lang2=target_lang, split="train")
dataset

Downloading:   0%|          | 0.00/2.08k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/7.41k [00:00<?, ?B/s]

Using custom data configuration ar-en-lang1=ar,lang2=en


Downloading:   0%|          | 0.00/24.7M [00:00<?, ?B/s]

0 examples [00:00, ? examples/s]

Dataset news_commentary downloaded and prepared to /root/.cache/huggingface/datasets/news_commentary/ar-en-lang1=ar,lang2=en/0.0.0/cfab724ce975dc2da51cdae45302389860badc88b74db8570d561ced6004f8b4. Subsequent calls will reuse this data.


Dataset({
    features: ['id', 'translation'],
    num_rows: 83187
})

We see that the data is quite large - it has over a million translations. Since it's only text data, it should be relatively easy to process though.

Next, let's look at how the data was preprocessed when training the fine-tuned *XLS-R* checkpoint in Swedish. Looking at the [`run.sh` file](https://huggingface.co/hf-test/xls-r-300m-sv/blob/main/run.sh), we can see that the following characters were removed from the official transcriptions:

In [5]:
chars_to_ignore_regex = '[,?.!\-\;\:\"“%‘”�—’…–]'  # change to the ignored characters of your fine-tuned model

Let's do the same here so that the alphabet of our language model matches the one of the fine-tuned acoustic checkpoints.

We can write a single map function to extract the Swedish text and process it right away.

In [6]:
import re
alpha_numerical = "[0-9A-Za-z]"
def extract_text(batch):
    text = batch["translation"]['ar']
    batch["text"] = re.sub(chars_to_ignore_regex, "", text.lower())
    batch["text"] = re.sub(alpha_numerical, "",batch["text"])
    batch["text"] = re.sub("[—]", '', batch["text"])
    batch["text"] = re.sub("[_]", '', batch["text"])
    batch["text"] = re.sub("[«]", '', batch["text"])
    batch["text"] = re.sub("[»]", '', batch["text"])
    # batch["sentence"] = re.sub("['ِ]", '', batch["sentence"])
    batch["text"] = re.sub("[،]", '', batch["text"])
    batch["text"] = re.sub("[؛]", '', batch["text"])
    batch["text"] = re.sub("[؟]", '', batch["text"])
    batch["text"] = re.sub("['ۖ]", '', batch["text"])
    batch["text"] = re.sub("[ـ]", '', batch["text"])
    batch["text"] = re.sub("[☭]", '', batch["text"])
    batch["text"] = re.sub("[…]", '', batch["text"])
    batch["text"] = re.sub("['ۗ]", '', batch["text"])
    batch["text"] = re.sub("[،]", '', batch["text"])
    batch["text"] = re.sub("[؛]", '', batch["text"])
    batch["text"] = re.sub("['ۘ]", '', batch["text"])
    batch["text"] = re.sub("['ۚ]", '', batch["text"])
    batch["text"] = re.sub("['ۛ]", '', batch["text"])
    batch["text"] = re.sub("['ً]", '', batch["text"])
    batch["text"] = re.sub("['ٌ]", '', batch["text"])
    batch["text"] = re.sub("['ٍ]", '', batch["text"])
    batch["text"] = re.sub("['ّ]", '', batch["text"])
    batch["text"] = re.sub("['ٰ]", '', batch["text"])
    return batch

Let's apply the `.map()` function. This should take roughly 5 minutes.

In [7]:
dataset = dataset.map(extract_text, remove_columns=dataset.column_names)
dataset

0ex [00:00, ?ex/s]

Dataset({
    features: ['text'],
    num_rows: 83187
})

Great. Our dataset is already finished. Let's upload it to the Hub so that we can inspect and reuse it better.

You can log in by executing the following cell.

In [4]:
from huggingface_hub import notebook_login

notebook_login()

Next, we call 🤗 Hugging Face's [`push_to_hub`](https://huggingface.co/docs/datasets/package_reference/main_classes.html?highlight=push#datasets.Dataset.push_to_hub) method to upload the dataset to the repo `"swedish_corpora_parliament_processed"`.

In [9]:
dataset.push_to_hub(f"ar_corpora_parliament_processed", split="train")

The repository already exists: the `private` keyword argument will be ignored.


Pushing dataset shards to the dataset hub:   0%|          | 0/1 [00:00<?, ?it/s]

That was easy! The dataset viewer is automatically enabled when uploading a new dataset, which is very convenient. You can now directly inspect the dataset online. 

Feel free to look through our preprocessed dataset directly on [`hf-test/sv_corpora_parliament_processed`](https://huggingface.co/datasets/hf-test/sv_corpora_parliament_processed). Even if we are not a native speaker in Swedish, we can see that the data is well processed and seems clean.

Next, let's use the data to build a language model.

## **3. Build an *n-gram* with KenLM**

While large language models based on the [Transformer architecture](https://jalammar.github.io/illustrated-transformer/) have become the standard in NLP, it is still very common to use an ***n-gram*** LM to boost speech recognition systems - as shown in Section 1.

Looking again at Table 9 of Appendix C of the [official Wav2Vec2 paper](https://arxiv.org/abs/2006.11477), it can be noticed that using a *Transformer*-based LM for decoding clearly yields better results than using an *n-gram* model, but the difference between *n-gram* and *Transformer*-based LM is much less significant than the difference between *n-gram* and no LM. 

*E.g.*, for the large Wav2Vec2 checkpoint that was fine-tuned on 10min only, an *n-gram* reduces the word error rate (WER) compared to no LM by *ca.* 80% while a *Transformer*-based LM *only* reduces the WER by another 23% compared to the *n-gram*. This relative WER reduction becomes less, the more data the acoustic model has been trained on. *E.g.*, for the large checkpoint a *Transformer*-based LM reduces the WER by merely 8% compared to an *n-gram* LM whereas the *n-gram* still yields a 21% WER reduction compared to no language model.

The reason why an *n-gram* is preferred over a *Transformer*-based LM is that *n-grams* come at a significantly smaller computational cost. For an *n-gram*, retrieving the probability of a word given previous words is almost only as computationally expensive as querying a look-up table or tree-like data storage - *i.e.* it's very fast compared to modern *Transformer*-based language models that would require a full forward pass to retrieve the next word probabilities.

For more information on how *n-grams* function and why they are (still) so useful for speech recognition, the reader is advised to take a look at [this excellent summary](https://web.stanford.edu/~jurafsky/slp3/3.pdf) from Stanford.

Great, let's see step-by-step how to build an *n-gram*. We will use the popular [KenLM library](https://github.com/kpu/kenlm) to do so. Let's start by installing the Ubuntu library prerequisites:

In [ ]:
import getpass
import os

password = getpass.getpass()
command = "sudo -S apt-get update" # can be any command but don't forget -S as it enables input from stdin
os.popen(command, 'w').write(password+'\n') # newline char is important otherwise prompt will wait for you to manually perform newline

 ·····································


/bin/sh: line 1: sudo: command not found


38

In [12]:
!sudo apt-get install build-essential cmake libboost-system-dev libboost-thread-dev libboost-program-options-dev libboost-test-dev libeigen3-dev zlib1g-dev libbz2-dev liblzma-dev

Reading package lists... Done
Building dependency tree       
Reading state information... Done
build-essential is already the newest version (12.4ubuntu1).
libboost-program-options-dev is already the newest version (1.65.1.0ubuntu1).
libboost-program-options-dev set to manually installed.
libboost-system-dev is already the newest version (1.65.1.0ubuntu1).
libboost-system-dev set to manually installed.
libboost-thread-dev is already the newest version (1.65.1.0ubuntu1).
libboost-thread-dev set to manually installed.
liblzma-dev is already the newest version (5.2.2-1.3).
liblzma-dev set to manually installed.
zlib1g-dev is already the newest version (1:1.2.11.dfsg-0ubuntu2).
zlib1g-dev set to manually installed.
libboost-test-dev is already the newest version (1.65.1.0ubuntu1).
libboost-test-dev set to manually installed.
cmake is already the newest version (3.10.2-1ubuntu2.18.04.2).
libbz2-dev is already the newest version (1.0.6-8.1ubuntu0.2).
libbz2-dev set to manually installed.
Th

before downloading and unpacking the KenLM repo.

In [13]:
!wget -O - https://kheafield.com/code/kenlm.tar.gz | tar xz

--2022-02-05 04:53:46--  https://kheafield.com/code/kenlm.tar.gz
Resolving kheafield.com (kheafield.com)... 35.196.63.85
Connecting to kheafield.com (kheafield.com)|35.196.63.85|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 491090 (480K) [application/x-gzip]
Saving to: ‘STDOUT’

-                   100%[===================>] 479.58K  1.67MB/s    in 0.3s    

2022-02-05 04:53:47 (1.67 MB/s) - written to stdout [491090/491090]



KenLM is written in C++, so we'll make use of `cmake` to build the binaries.

In [14]:
!mkdir kenlm/build && cd kenlm/build && cmake .. && make -j2
!ls kenlm/build/bin

-- The C compiler identification is GNU 7.5.0
-- The CXX compiler identification is GNU 7.5.0
-- Check for working C compiler: /usr/bin/cc
-- Check for working C compiler: /usr/bin/cc -- works
-- Detecting C compiler ABI info
-- Detecting C compiler ABI info - done
-- Detecting C compile features
-- Detecting C compile features - done
-- Check for working CXX compiler: /usr/bin/c++
-- Check for working CXX compiler: /usr/bin/c++ -- works
-- Detecting CXX compiler ABI info
-- Detecting CXX compiler ABI info - done
-- Detecting CXX compile features
-- Detecting CXX compile features - done
-- Looking for pthread.h
-- Looking for pthread.h - found
-- Looking for pthread_create
-- Looking for pthread_create - not found
-- Looking for pthread_create in pthreads
-- Looking for pthread_create in pthreads - not found
-- Looking for pthread_create in pthread
-- Looking for pthread_create in pthread - found
-- Found Threads: TRUE  
-- Boost version: 1.65.1
-- Found the following Boost libraries:


Great, as we can see, the executable functions have successfully been built under `kenlm/build/bin/`.

KenLM by default computes an *n-gram* with [Kneser-Ney smooting](https://en.wikipedia.org/wiki/Kneser%E2%80%93Ney_smoothing). All text data used to create the *n-gram* is expected to be stored in a text file.
We download our dataset and save it as a `.txt` file.

In [15]:
from datasets import load_dataset

username = "kingabzpro"  # change to your username

dataset = load_dataset(f"{username}/ar_corpora_parliament_processed", split="train")

with open("text.txt", "w") as file:
  file.write(" ".join(dataset["text"]))

Downloading:   0%|          | 0.00/1.67k [00:00<?, ?B/s]

Using custom data configuration kingabzpro--ar_corpora_parliament_processed-7ee75506d2f6dcc4


  0%|          | 0/1 [00:00<?, ?it/s]

Downloading:   0%|          | 0.00/25.5M [00:00<?, ?B/s]

  0%|          | 0/1 [00:00<?, ?it/s]

Dataset parquet downloaded and prepared to /root/.cache/huggingface/datasets/parquet/kingabzpro--ar_corpora_parliament_processed-7ee75506d2f6dcc4/0.0.0/0b6d5799bb726b24ad7fc7be720c170d8e497f575d02d47537de9a5bac074901. Subsequent calls will reuse this data.


Now, we just have to run KenLM's `lmplz` command to build our *n-gram*, called `"5gram.arpa"`. As it's relatively common in speech recognition, we build a *5-gram* by passing the `-o 5` parameter.
For more information on the different *n-gram* LM that can be built 
with KenLM, one can take a look at the [official website of KenLM](https://kheafield.com/code/kenlm/).

Executing the command below might take a minute or so.

In [16]:

!kenlm/build/bin/lmplz -o 5 <"text.txt" > "5gram.arpa"

=== 1/5 Counting and sorting n-grams ===
Reading /content/text.txt
----5---10---15---20---25---30---35---40---45---50---55---60---65---70---75---80---85---90---95--100
tcmalloc: large alloc 1918697472 bytes == 0x55e8ed702000 @  0x7f5cedcad1e7 0x55e8ec2557a2 0x55e8ec1f051e 0x55e8ec1cf2eb 0x55e8ec1bb066 0x7f5cebe46bf7 0x55e8ec1bcbaa
tcmalloc: large alloc 8953896960 bytes == 0x55e95fcd2000 @  0x7f5cedcad1e7 0x55e8ec2557a2 0x55e8ec2447ca 0x55e8ec245208 0x55e8ec1cf308 0x55e8ec1bb066 0x7f5cebe46bf7 0x55e8ec1bcbaa
****************************************************************************************************
Unigram tokens 4953590 types 154929
=== 2/5 Calculating and sorting adjusted counts ===
Chain sizes: 1:1859148 2:1063013888 3:1993151104 4:3189041664 5:4650685952
tcmalloc: large alloc 4650688512 bytes == 0x55e8ed702000 @  0x7f5cedcad1e7 0x55e8ec2557a2 0x55e8ec2447ca 0x55e8ec245208 0x55e8ec1cf8d7 0x55e8ec1bb066 0x7f5cebe46bf7 0x55e8ec1bcbaa
tcmalloc: large alloc 1993154560 bytes == 0

Great, we have built a *5-gram* LM! Let's inspect the first couple of lines.

In [17]:
!head -20 5gram.arpa

\data\
ngram 1=154928
ngram 2=1951043
ngram 3=3808342
ngram 4=4594632
ngram 5=4848900

\1-grams:
-6.2970614	<unk>	0
0	<s>	-0.09341879
-4.2426977	الذهب	-0.2197705
-5.265963	بعشرة	-0.1773004
-4.3284874	آلاف	-0.29791862
-4.0686555	دولار	-0.33736664
-4.603849	سان	-0.4746134
-5.4108515	فرانسيسكو	-0.11966315
-2.7832785	لم	-0.62132126
-4.8193336	يكن	-0.12888719
-1.9863459	من	-0.8163693
-4.8497424	السهل	-0.14798915


There is a small problem that 🤗 Transformers will not be happy about later on.
The *5-gram* correctly includes a "Unknown" or `<unk>`, as well as a *begin-of-sentence*, `<s>` token, but no *end-of-sentence*, `</s>` token.
This sadly has to be corrected currently after the build.

We can simply add the *end-of-sentence* token by adding the line `0 </s>  -0.11831701` below the *begin-of-sentence* token and increasing the `ngram 1` count by 1. Because the file has roughly 100 million lines, this command will take *ca.* 2 minutes.

In [18]:
with open("5gram.arpa", "r") as read_file, open("5gram_correct.arpa", "w") as write_file:
  has_added_eos = False
  for line in read_file:
    if not has_added_eos and "ngram 1=" in line:
      count=line.strip().split("=")[-1]
      write_file.write(line.replace(f"{count}", f"{int(count)+1}"))
    elif not has_added_eos and "<s>" in line:
      write_file.write(line)
      write_file.write(line.replace("<s>", "</s>"))
      has_added_eos = True
    else:
      write_file.write(line)

Let's now inspect the corrected *5-gram*.

In [19]:
!head -20 5gram_correct.arpa

\data\
ngram 1=154929
ngram 2=1951043
ngram 3=3808342
ngram 4=4594632
ngram 5=4848900

\1-grams:
-6.2970614	<unk>	0
0	<s>	-0.09341879
0	</s>	-0.09341879
-4.2426977	الذهب	-0.2197705
-5.265963	بعشرة	-0.1773004
-4.3284874	آلاف	-0.29791862
-4.0686555	دولار	-0.33736664
-4.603849	سان	-0.4746134
-5.4108515	فرانسيسكو	-0.11966315
-2.7832785	لم	-0.62132126
-4.8193336	يكن	-0.12888719
-1.9863459	من	-0.8163693


Great, this looks better! We're done at this point and all that is left to do is to correctly integrate the `"ngram"` with [`pyctcdecode`](https://github.com/kensho-technologies/pyctcdecode) and 🤗 Transformers.

## **4. Combine an *n-gram* with Wav2Vec2**

In a final step, we want to wrap the *5-gram* into a `Wav2Vec2ProcessorWithLM` object to make the *5-gram* boosted decoding as seamless as shown in Section 1.
We start by downloading the currently "LM-less" processor of [`xls-r-300m-sv`](https://huggingface.co/hf-test/xls-r-300m-sv).

In [20]:
from transformers import AutoProcessor

processor = AutoProcessor.from_pretrained("kingabzpro/wav2vec2-large-xlsr-300-arabic")

Downloading:   0%|          | 0.00/214 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/181 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.02k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/520 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/85.0 [00:00<?, ?B/s]

Next, we extract the vocabulary of its tokenizer as it represents the `"labels"` of `pyctcdecode`'s `BeamSearchDecoder` class.

In [21]:
vocab_dict = processor.tokenizer.get_vocab()
sorted_vocab_dict = {k.lower(): v for k, v in sorted(vocab_dict.items(), key=lambda item: item[1])}

The `"labels"` and the previously built `5gram_correct.arpa` file is all that's needed to build the decoder. 

In [22]:
from pyctcdecode import build_ctcdecoder

decoder = build_ctcdecoder(
    labels=list(sorted_vocab_dict.keys()),
    kenlm_model_path="5gram_correct.arpa",
)

Found entries of length > 1 in alphabet. This is unusual unless style is BPE, but the alphabet was not recognized as BPE type. Is this correct?
Unigrams and labels don't seem to agree.


We can safely ignore the warning and all that is left to do now is to wrap the just created `decoder`, together with the processor's `tokenizer` and `feature_extractor` into a `Wav2Vec2ProcessorWithLM` class.

In [23]:
from transformers import Wav2Vec2ProcessorWithLM

processor_with_lm = Wav2Vec2ProcessorWithLM(
    feature_extractor=processor.feature_extractor,
    tokenizer=processor.tokenizer,
    decoder=decoder
)

We want to directly upload the LM-boosted processor into 
the model folder of [`xls-r-300m-sv`](https://huggingface.co/hf-test/xls-r-300m-sv) to have all relevant files in one place.

Let's clone the repo, add the new decoder files and upload them afterward.
First, we need to install `git-lfs`.

In [24]:
!sudo apt-get install git-lfs tree

Reading package lists... Done
Building dependency tree       
Reading state information... Done
The following packages were automatically installed and are no longer required:
  cuda-command-line-tools-10-0 cuda-command-line-tools-10-1
  cuda-command-line-tools-11-0 cuda-compiler-10-0 cuda-compiler-10-1
  cuda-compiler-11-0 cuda-cuobjdump-10-0 cuda-cuobjdump-10-1
  cuda-cuobjdump-11-0 cuda-cupti-10-0 cuda-cupti-10-1 cuda-cupti-11-0
  cuda-cupti-dev-11-0 cuda-documentation-10-0 cuda-documentation-10-1
  cuda-documentation-11-0 cuda-documentation-11-1 cuda-gdb-10-0 cuda-gdb-10-1
  cuda-gdb-11-0 cuda-gpu-library-advisor-10-0 cuda-gpu-library-advisor-10-1
  cuda-libraries-10-0 cuda-libraries-10-1 cuda-libraries-11-0
  cuda-memcheck-10-0 cuda-memcheck-10-1 cuda-memcheck-11-0 cuda-nsight-10-0
  cuda-nsight-10-1 cuda-nsight-11-0 cuda-nsight-11-1 cuda-nsight-compute-10-0
  cuda-nsight-compute-10-1 cuda-nsight-compute-11-0 cuda-nsight-compute-11-1
  cuda-nsight-systems-10-1 cuda-nsight-systems-

Cloning and uploading of modeling files can be done conveniently with the `huggingface_hub`'s `Repository` class. 

More information on how to use the `huggingface_hub` to upload any files, please take a look at the [official docs](https://huggingface.co/docs/hub/how-to-upstream).

In [3]:
from huggingface_hub import Repository

repo = Repository(local_dir="wav2vec2-large-xlsr-300-arabic", clone_from="kingabzpro/wav2vec2-large-xlsr-300-arabic")

Cloning https://huggingface.co/kingabzpro/wav2vec2-large-xlsr-300-arabic into local empty directory.


Download file pytorch_model.bin:   0%|          | 1.58k/1.18G [00:00<?, ?B/s]

Download file training_args.bin: 100%|##########| 2.98k/2.98k [00:00<?, ?B/s]

Clean file training_args.bin:  34%|###3      | 1.00k/2.98k [00:00<?, ?B/s]

Download file language_model/5gram.bin:   0%|          | 1.58k/326M [00:00<?, ?B/s]

Clean file language_model/5gram.bin:   0%|          | 1.00k/326M [00:00<?, ?B/s]

Clean file pytorch_model.bin:   0%|          | 1.00k/1.18G [00:00<?, ?B/s]

Having cloned `xls-r-300m-sv`, let's save the new processor with LM into it.

In [26]:
processor_with_lm.save_pretrained("wav2vec2-large-xlsr-300-arabic")

Let's inspect the local repository. The `tree` command conveniently can also show the size of the different files.

In [27]:
!tree -h wav2vec2-large-xlsr-300-arabic/

wav2vec2-large-xlsr-300-arabic/
├── [ 533]  alphabet.json
├── [2.0K]  config.json
├── [4.0K]  language_model
│   ├── [898M]  5gram_correct.arpa
│   ├── [  78]  attrs.json
│   └── [2.0M]  unigrams.txt
├── [ 262]  preprocessor_config.json
├── [1.2G]  pytorch_model.bin
├── [2.4K]  README.md
├── [  85]  special_tokens_map.json
├── [ 510]  tokenizer_config.json
├── [3.0K]  training_args.bin
└── [ 520]  vocab.json

1 directory, 12 files


As can be seen the *5-gram* LM is quite large - it amounts to more than 4 GB.
To reduce the size of the *n-gram* and make loading faster, `kenLM` allows converting `.arpa` files to binary ones using the `build_binary` executable.

Let's make use of it here.

In [28]:
!kenlm/build/bin/build_binary wav2vec2-large-xlsr-300-arabic/language_model/5gram_correct.arpa wav2vec2-large-xlsr-300-arabic/language_model/5gram.bin

Reading wav2vec2-large-xlsr-300-arabic/language_model/5gram_correct.arpa
----5---10---15---20---25---30---35---40---45---50---55---60---65---70---75---80---85---90---95--100
****************************************************************************************************
SUCCESS


Great, it worked! Let's remove the `.arpa` file and check the size of the binary *5-gram* LM.

In [29]:
!rm wav2vec2-large-xlsr-300-arabic/language_model/5gram_correct.arpa && tree -h wav2vec2-large-xlsr-300-arabic/

wav2vec2-large-xlsr-300-arabic/
├── [ 533]  alphabet.json
├── [2.0K]  config.json
├── [4.0K]  language_model
│   ├── [326M]  5gram.bin
│   ├── [  78]  attrs.json
│   └── [2.0M]  unigrams.txt
├── [ 262]  preprocessor_config.json
├── [1.2G]  pytorch_model.bin
├── [2.4K]  README.md
├── [  85]  special_tokens_map.json
├── [ 510]  tokenizer_config.json
├── [3.0K]  training_args.bin
└── [ 520]  vocab.json

1 directory, 12 files


Nice, we reduced the *n-gram* by more than half to less than 2GB now. In the final step, let's upload all files.

In [8]:
repo.push_to_hub(commit_message="Eval-results")

FileNotFoundError: [Errno 2] No such file or directory: '/workspace/wav2vec2-large-xlsr-300-arabic/".ipynb_checkpoints/Boosting_Wav2Vec2_with_n_grams_in_\\360\\237\\244\\227_Transformers_(1)-checkpoint.ipynb"'

In [5]:
!python eval.py --model_id kingabzpro/wav2vec2-large-xlsr-300-arabic --dataset mozilla-foundation/common_voice_7_0 --config ar --split test


Downloading: 100%|█████████████████████████| 9.88k/9.88k [00:00<00:00, 5.92MB/s]
Downloading: 100%|█████████████████████████| 2.98k/2.98k [00:00<00:00, 1.83MB/s]
Downloading: 100%|█████████████████████████| 49.7k/49.7k [00:00<00:00, 1.72MB/s]
Downloading: 100%|█████████████████████████| 2.95G/2.95G [02:10<00:00, 22.5MB/s]
Dataset common_voice downloaded and prepared to /workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/ar/7.0.0/fe20cac47c166e25b1f096ab661832e3da7cf298ed4a91dcaa1343ad972d175b. Subsequent calls will reuse this data.
Downloading: 100%|██████████████████████████| 2.02k/2.02k [00:00<00:00, 887kB/s]
Downloading: 100%|██████████████████████████████| 262/262 [00:00<00:00, 166kB/s]
Downloading: 100%|█████████████████████████| 1.18G/1.18G [00:18<00:00, 69.7MB/s]
Downloading: 100%|██████████████████████████████| 520/520 [00:00<00:00, 344kB/s]
Downloading: 100%|███████████████████████████| 85.0/85.0 [00:00<00:00, 53.8kB/s]
Downloading: 100%|██████████████████

That's it. Now you should be able to use the *5gram* for LM-boosted decoding as shown in Section 1.

As can be seen on [`xls-r-300m-sv`'s model card](https://huggingface.co/hf-test/xls-r-300m-sv#inference-with-lm) our *5gram* LM-boosted decoder yields a WER of 18.85% on Common Voice's 7 test set which is a relative performance of *ca.* 30% 🔥.